In [6]:
!pip install huggingface_hub>=0.15.0
!pip install gradio>=3.50.0
!pip install accelerate===0.27.2
!pip install diffusers>=0.21.0
!pip install invisible_watermark
!pip install torch>=2.0.0
!pip install transformers>=4.30.0
!pip install pillow>=9.0.0
!pip install xformers
!pip install bitsandbytes
!pip install datasets

import os
import gradio as gr
import torch
from diffusers import DiffusionPipeline
from transformers import BitsAndBytesConfig
from datasets import load_dataset
from PIL import Image

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.1/69.1 MB 10.6 MB/s eta 0:00:00


In [7]:
# Limpar o cache da GPU
torch.cuda.empty_cache()

# Enable memory pool expansion
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

# Definir a configuração de alocação de memória
torch.cuda.set_per_process_memory_fraction(0.8)  # Usar 80% da memória da GPU


In [8]:
# Configurações do dispositivo para uso apenas da CPU
device = "cuda"
model_repo_id = "stabilityai/stable-diffusion-xl-base-1.0"  # Continuando com o modelo especificado

In [11]:
# Load the model in 8-bit precision
bnb_config = BitsAndBytesConfig(
    load_in_8bit=True,  # Load the model in 8-bit precision
    bnb_8bit_compute_dtype=torch.float16,  # Use float16 for computation
    bnb_8bit_use_double_quant=True,  # Enable double quantization for better performance
)

Unused kwargs: ['bnb_8bit_compute_dtype', 'bnb_8bit_use_double_quant']. These kwargs are not used in <class 'transformers.utils.quantization_config.BitsAndBytesConfig'>.


In [12]:
# Carregar o pipeline configurado para CPU
pipe = DiffusionPipeline.from_pretrained(model_repo_id, torch_dtype=torch.float16,variant="fp16",use_auth_token=True,)
pipe = pipe.to(device)


Fetching 19 files:   0%|          | 0/19 [00:00<?, ?it/s]

diffusion_pytorch_model.fp16.safetensors:   0%|          | 0.00/167M [00:00<?, ?B/s]

model.fp16.safetensors:   0%|          | 0.00/1.39G [00:00<?, ?B/s]

model.fp16.safetensors:   0%|          | 0.00/246M [00:00<?, ?B/s]

diffusion_pytorch_model.fp16.safetensors:   0%|          | 0.00/5.14G [00:00<?, ?B/s]

diffusion_pytorch_model.fp16.safetensors:   0%|          | 0.00/167M [00:00<?, ?B/s]

Keyword arguments {'use_auth_token': True} are not expected by StableDiffusionXLPipeline and will be ignored.


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

In [13]:
# Carregando o dataset do Hugging Face
dataset = load_dataset("LEIDIA/Data_Womleimg")


# Parâmetros para carregar o dataset personalizado
dataset_descriptions = [
    "Images/Image01.jpg,A blonde woman wearing a blue leather jumpsuit with leather gloves the same color. She is standing with one hand on her face and the other on her waist, in a confident pose.  The background is dark and neutral, highlighting the woman figure.",
    "Images/Image02.jpg,A woman standing in an urban environment, possibly a street between buildings.She is dressed in a long-sleeved white blouse and tight black leather pants, with a wide belt at her waist.  She wears high black boots and has long, loose hair.  The background includes buildings and a street, suggesting an urban setting",
    "Images/Image03.jpg,A woman legs wearing blue high leather boots with a zipper on the side and high heels.The background is a light blue color, highlighting the boots. The woman legs is standing, with slightly apart, showing her boots prominently.",
    "Images/Image04.jpg,A brunette woman wearing a long red leather coat combined with a leather shorts and tigh high leather boots of the same color. The coat is open, revealing the skirt and boots. The background is neutral and blurred, highlighting the woman figure.",
    "Images/Image05.jpg,The image shows the lower part of a woman body, seen from the side. She is wearing tight beige leather pants and black high-heeled boots. is leaning against a brick wall, and the background includes a glass door. The lighting is natural, highlighting the woman curves and clothing.",
    "Images/Image06.jpg,A woman in purple leather leggings with tigh high black leather boots",
    "Images/Image07.jpg,A woman in black leather top and a long black leather skirt",
    "Images/Image08.jpg,A blonde long hair curly woman using a yellow mini tight leather skirt",
    "Images/Image09.jpg,A thin asian woman using a thigh long black leather dress",
    "Images/Image10.jpg,A simple high brown leather boots",
    "Images/Image11.jpg,A beautiful face brunette woman using a leather clothes",
    "Images/Image12.jpg,A beautiful brunette woman wearing a sleeveless black dress, seated at a bar, She is holding a glass champagne, The background is softly lit, with warm lighting and blurred bottles on shelves, creating a cozy and elegant atmosphere.",
    "Images/Image13.jpg,A curly blonde woman is wearing a bold and stylish outfit red leather jacket paired with black leather tight pants and red high-heeled leather boots, The outfit has a modern and edgy vibe, with a focus on vibrant colors and sleek materials.",
    "Images/Image14.jpg,Ebony woman standing outdoors against a backdrop of rolling hills and a cloudy sky,wearing a striking outfit consisting of a red leather shirt, a black leather mini corset, and a red plaid skirt with a long panel on one side,also wearing knee-high red lace-up leather boots, Their hair is voluminous and styled in natural curls, The setting appears to be a grassy landscape.",
    "Images/Image15.jpg,Blonde curly woman is wearing a fitted, shiny blue outfit made of what appears to be leather or vinyl clothes, The ensemble includes a jacket and pants with metallic buttons and a belt at the waist, They are also wearing knee-high boots with lacing details, Their hair is styled in voluminous, curly blonde locks. The setting is a simple, neutral-colored room with a concrete or stone-like wall and floor.",
    "Images/Image16.jpg,The girl is wearing a black leather outfit include top,legging and sleeves,consisting of a fitted top with a heart-shaped cutout and high-waisted pants, The ensemble includes a purple cape and the individual has long purple hair,The style is reminiscent of superhero or fantasy attire, emphasizing a bold and sleek look.",
    "Images/Image17.jpg,The girl dressed in a sleek, black leather outfit. The attire includes a cropped top with a zip closure and a high-waisted bottom, both designed to accentuate the figure silhouette, The individual has long, pink hair styled in a ponytail, and is wearing long black gloves that reach the upper arms. The background appears to be softly lit, enhancing the glossy texture of the leather. The overall look is bold and fashion-forward, with a striking color contrast between the black and pink elements.",
    "Images/Image18.jpg,a girl wearing a form-fitting black leather top that highlights their physique, The top has a high neckline and is sleeveless, emphasizing the shoulders and arms, The individual has long, pink hair cascading down, adding a striking contrast to the outfit. The background is a light, neutral color, which helps to accentuate the subject, The overall aesthetic is bold and fashion-forward.",
    "Images/Image19.jpg,a brunette girl wearing a black leather top and matching black leather pants with a decorative button on the waist. It presented in a stylish, modern pose against a gray background",
    "Images/Image20.jpg,a young asian woman standing inside a subway car or train.  She is leaning on one of the vertical poles of the car, with her arms crossed.  The woman is dressed in a white short-sleeved t-shirt and a black leather shorts.  Her hair is long and dark, and she appears to be looking to the side, with a serious or thoughtful expression.",
    "Images/Image21.jpg,a young asian woman in a subway or train environment.  She is standing near the carriage doors, with one hand resting on her hip and the other at her side.  The woman is dressed in a tight white tank top and black leather pants.  Her hair is long, straight and dark, and she is looking directly at the camera with a serious expression.",
    "Images/Image22.jpg,a young brunette woman posing with her back to the camera, with her face turned to the side. She is dressed in a black leather top and tight black leather pants, as well as black leather gloves.  His hair is long and wavy, with light highlights.The pose and outfit suggest a sensual and modern style, possibly for a fashion photo shoot or a themed shoot.",
    "Images/Image23.jpg,The image shows a part of a woman body, specifically the butt region and part of the thighs. The woman is wearing a white thigh leather pants. The outfit has a cut that highlights the curves of the body and includes a wide belt at the waist with metallic details.The background of the image is neutral and blurred, which helps to highlight the clothing and body shape, The lighting is soft and even, enhancing the texture and shine of the clothing material.  The pose and choice of clothing suggest a modern and sensual style, possibly for a fashion photo shoot or a themed shoot.The image focuses on the silhouette and curves of the body, highlighting the model clothes and physical shape.",
    "Images/Image24.jpg,This image shows a part of a woman body, specifically the butt region and part of the thighs,seen from the side.The woman is wearing a white tight leather pants,The clothing has visible seams that highlight the body curves.The belt at the waist is wide and has metallic details, including a small clasp or button.  The background of the image is neutral and blurred, which helps to highlight the clothing and body shape. The lighting is soft and even, enhancing the texture and shine of the clothing material.The image focuses on the silhouette and curves of the body, highlighting the model clothes and physical shape.  The choice of material and design of the clothing, combined with the model pose, conveys a feeling of elegance and sophistication.",
    "Images/Image25.jpg,shows a woman lower body seen from behind, a beautiful butt in shape,She is wearing a tight white leather pants that highlights your curves,The outfit has visible seams and a wide belt at the waist. The background is neutral and blurred, highlighting the woman silhouette.",
    "Images/Image26.jpg,a woman from behind, dressed in a tight-fitting outfit made of gray leather clothes, The outfit includes details that resemble armor, such as shoulder pads and a wide belt with a buckle.  The woman hair is tied up in a high ponytail, and she is looking to the side. The background is neutral and blurred, highlighting the woman figure.",
    "Images/Image27.jpg,a woman sitting in a chair, dressed in a black blazer and purple leather pants, She is wearing black high-heeled leather boots and a black choker. Her hair is blonde and wavy, and she is looking directly into the camera.  The background is neutral and blurred, highlighting the woman figure.",
    "Images/Image28.jpg,a woman posing on an urban street.  She is dressed in a black leather jacket, black leather pants, and tall boots with buckle details.  Her hair is blonde and wavy curly, and she wears a light-colored T-shirt under her jacket.  The background includes a wooden door and a stone wall, suggesting an urban and historic environment.,"
    "Images/Image29.jpg,a blonde woman wearing a black leather zip-up jacket and tight black leather pants.  She is posing with one hand on her hip and the other holding the zipper of her jacket.  The background is a textured wall, and the lighting highlights the woman outfit and confident pose.",
    "Images/Image30.jpg,a blonde woman dressed in a black leather jacket, tight black leather pants, and thigh-high boots. She is standing with her legs apart and one hand on her waist, in a confident pose. The background appears to be a photography studio with concrete walls and visible equipment.",
    "Images/Image31.jpg,a blonde woman standing, dressed in a black leather jacket and tight black leather pants. The jacket has zippers and metallic details, and the woman has one hand in her pocket and the other at her side. She has blonde, wavy hair, and is looking directly at the camera with a confident expression. The background is neutral and blurred, highlighting the woman figure.",
    "Images/Image32.jpg,a woman standing, dressed in a long red leather coat, a short black leather skirt, black high boots and a black turtleneck.  She is holding a black bag and posing with one hand on her hip.  The background is neutral with red curtains, highlighting the woman and her clothes.",
    "Images/Image33.jpg,a woman on an urban street.  She is wearing a red leather coat open, revealing a top that exposes her abdomen, and a short dark red leather shorts. Her hair is long and loose, and she is wearing red lipstick. The background shows a busy street with blurred shops and people."
]

README.md:   0%|          | 0.00/42.0 [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/34 [00:00<?, ?it/s]

Image08.jpg:   0%|          | 0.00/57.2k [00:00<?, ?B/s]

Image07.jpg:   0%|          | 0.00/63.8k [00:00<?, ?B/s]

Image11.jpg:   0%|          | 0.00/76.7k [00:00<?, ?B/s]

...

Image23.jpg:   0%|          | 0.00/91.5k [00:00<?, ?B/s]

Image30.jpg:   0%|          | 0.00/139k [00:00<?, ?B/s]

Image32.jpg:   0%|          | 0.00/980k [00:00<?, ?B/s]

Image33.jpg:   0%|          | 0.00/1.31M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/33 [00:00<?, ? examples/s]

In [32]:
# Definir parâmetros padrão para geração rápida
DEFAULT_PROMPT = "A blonde long hair curly woman using a yellow mini tight leather skirt "
NEGATIVE_PROMPT = "bad anatomy, poorly drawn hands, poorly drawn feet, poorly drawn face, out of frame, extra limbs, disfigured, deformed, body out of frame, blurry, bad art, blurred, watermark, grainy, signature, cut off, draft, amateur, poorly drawn, childish, mutilated, 3D, CGI, anime, draw image"
DEFAULT_INFERENCE_STEPS = 95
IMAGE_WIDTH = 512
IMAGE_HEIGHT = 816
GUIDANCE_SCALE = 35

def resize_to_divisible_by_8(image):
    width, height = image.size
    new_width = width + (8 - width % 8) if width % 8 != 0 else width
    new_height = height + (8 - height % 8) if height % 8 != 0 else height
    return image.resize((new_width, new_height))

import tempfile


# Função simples para gerar imagem
def infer_simple(prompt):
    # Geração da imagem
    image = pipe(
        prompt=prompt,
        negative_prompt=NEGATIVE_PROMPT,
        num_inference_steps=DEFAULT_INFERENCE_STEPS,
        guidance_scale=GUIDANCE_SCALE,
        height=IMAGE_HEIGHT,
        width=IMAGE_WIDTH,
    ).images[0]
    # Redimensionar a imagem para ser divisível por 8
    image = resize_to_divisible_by_8(image)
    return image

    # Converter para JPG usando Pillow
    image = image.convert("RGB")  # Converter para modo RGB se necessário
    # Salvar em um buffer in-memory
    return image

    with tempfile.NamedTemporaryFile(suffix=".jpg", delete=False) as temp_file:
        image.save(temp_file.name)
        temp_filename = temp_file.name

    # Retornar o nome do arquivo temporário
    return temp_filename


# Interface Gradio
with gr.Blocks() as demo:
    with gr.Row():
        gr.Markdown("## Text-to-Image Wom Test - Cuda Version")


    prompt = gr.Textbox(
        label="Prompt",
        value=DEFAULT_PROMPT,
        placeholder="Describe the image you want to generate",
    )

    generate_button = gr.Button("Generate")
    result = gr.Image(label="Generated Image")

    generate_button.click(
        fn=infer_simple,
        inputs=prompt,
        outputs=result,
    )

if __name__ == "__main__":
    demo.launch(debug=True)


Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://90380e0b4f8c25e463.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


  0%|          | 0/95 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://90380e0b4f8c25e463.gradio.live
